In [1]:
import sys
sys.executable

'/ssd/anaconda-envs/gtsam/bin/python'

In [2]:
import numpy as np
import pandas as pd
import plotly.express as px
import plotly.graph_objects as go

In [17]:
data_num = 1
n_robots = 5
sample_time = 0.02
timesteps_per_frame = 100

In [4]:
def textread(filepath):
    """
    read from MRCLAM data in which every line
    contains equal number of values seperated by
    some whitespaces.
    """
    return np.array(pd.read_csv(filepath, 
                       sep = "\s+|\t+|\s+\t+|\t+\s+",
                       header=None,
                       comment='#',
                       engine='python'))

In [5]:
root = F'../MRCLAM_Dataset{data_num}/'
print('Parsing Dataset...')

print('\nReading barcode numbers...')
barcodes = textread(root + 'Barcodes.dat')
barcodes = np.array(barcodes)
print('Barcodes: (Subject, Barcode)')

print('\nReading landmark groundtruth...')
landmark_groundtruth = textread(root + 'Landmark_Groundtruth.dat')
n_landmarks = landmark_groundtruth.shape[0]
print(F'Landmark Groundtruth({landmark_groundtruth.shape}): (Subject, x [m], y [m], x std-dev [m], y std-dev [m])')


robots_data = {}
print('\nReading all robots data...')
print('robot groundtruth data((N, 4)): (Time [s], x [m], y [m], orientation [rad])')
print('robot odometry data((N, 3)): (Time [s], forward velocity [m/s], angular velocity [rad/s])')
print('robot measurement data((N, 3)): (Time [s], Subject, range [m], bearing [rad])\n')
for i in range(1, n_robots + 1):
    print(F'Reading robot{i} groundtruth...')
    robots_data[F'robot{i}_groundtruth'] = textread(root + F'Robot{i}_Groundtruth.dat')
    print(F'Reading robot{i} odometry...')
    robots_data[F'robot{i}_odometry'] = textread(root + F'Robot{i}_Odometry.dat')
    print(F'Reading robot{i} measurements...')
    robots_data[F'robot{i}_measurements'] = textread(root + F'Robot{i}_Measurement.dat')
    print('\n')

print('Parsing Complete')

Parsing Dataset...

Reading barcode numbers...
Barcodes: (Subject, Barcode)

Reading landmark groundtruth...
Landmark Groundtruth((15, 5)): (Subject, x [m], y [m], x std-dev [m], y std-dev [m])

Reading all robots data...
robot groundtruth data((N, 4)): (Time [s], x [m], y [m], orientation [rad])
robot odometry data((N, 3)): (Time [s], forward velocity [m/s], angular velocity [rad/s])
robot measurement data((N, 3)): (Time [s], Subject, range [m], bearing [rad])

Reading robot1 groundtruth...
Reading robot1 odometry...
Reading robot1 measurements...


Reading robot2 groundtruth...
Reading robot2 odometry...
Reading robot2 measurements...


Reading robot3 groundtruth...
Reading robot3 odometry...
Reading robot3 measurements...


Reading robot4 groundtruth...
Reading robot4 odometry...
Reading robot4 measurements...


Reading robot5 groundtruth...
Reading robot5 odometry...
Reading robot5 measurements...


Parsing Complete


In [7]:
# get the start and end time for the whole dataset
min_time, max_time = float('inf'), float('-inf')
for i in range(1, n_robots + 1):
    min_time = min(min_time, robots_data[F'robot{i}_groundtruth'][0, 0])
    max_time = max(max_time, robots_data[F'robot{i}_groundtruth'][-1, 0])
for data in robots_data.values():
    data[:, 0] -= min_time
total_time = max_time - min_time
timesteps = int(total_time // sample_time + 1)
print(F'start time: {min_time} [s]\nend time: {max_time} [s]\ntotal time: {total_time} [s]')
print(F'sampling time is {sample_time} [s] ({1 / sample_time} [Hz])')
print(F'Discretize to {timesteps} timesteps')

start time: 1248272263.325 [s]
end time: 1248273763.319 [s]
total time: 1499.9939999580383 [s]
sampling time is 0.02 [s] (50.0 [Hz])
Discretize to 75000 timesteps


In [8]:
for data_name in robots_data:
    print(F'Processing {data_name}')
    data = robots_data[data_name]
    if 'groundtruth' in data_name or 'odometry' in data_name:
        # linear interpolation for groundtruth and odometry data
        rows, cols = data.shape
        sampling_data = np.zeros((timesteps, cols))
        k, i = 0, 0
        for k in range(timesteps):
            t = k * sample_time
            sampling_data[k, 0] = t
            while i < rows - 1 and data[i, 0] <= t:
                i += 1
            if i == 0 or i == rows - 1:
                if 'groundtruth' in data_name:
                    sampling_data[k, 1:] = data[i, 1:]
            else:
                p = (t - data[i - 1, 0]) / (data[i, 0] - data[i - 1, 0])
                for c in range(1, cols):
                    sampling_data[k, c] = p * (data[i, c] - data[i - 1, c]) + data[i - 1, c]
        robots_data[data_name] = sampling_data
    else:
        # for measurements, just round the measurement time
        # to nearest sampling time, and keep other data untouched
        data[:, 0] = np.round(data[:, 0] / sample_time) * sample_time

Processing robot1_groundtruth
Processing robot1_odometry
Processing robot1_measurements
Processing robot2_groundtruth
Processing robot2_odometry
Processing robot2_measurements
Processing robot3_groundtruth
Processing robot3_odometry
Processing robot3_measurements
Processing robot4_groundtruth
Processing robot4_odometry
Processing robot4_measurements
Processing robot5_groundtruth
Processing robot5_odometry
Processing robot5_measurements


In [10]:
robots_groundtruth_df = pd.DataFrame()
for i in range(1, n_robots + 1):
    groundtruth = robots_data[F'robot{i}_groundtruth']
    df = pd.DataFrame(data=groundtruth[::timesteps_per_frame, :3], columns=['timestep [s]', 'x [m]', 'y [m]'])
    df['name'] = F'robot{i}'
    robots_groundtruth_df = robots_groundtruth_df.append(df, ignore_index=True)
print(len(robots_groundtruth_df))

1875


In [15]:
fig = px.scatter(robots_groundtruth_df, x="x [m]", y="y [m]",
                 animation_frame="timestep [s]",
                 animation_group="name",
                 color="name", hover_name="name",
                 range_x=[-2, 6], range_y=[-6, 7])
fig.update_traces(marker=dict(size=13, line=dict(color='black', width=2)))
fig.add_trace(
    go.Scatter(
        mode='markers',
        x=landmark_groundtruth[:, 1],
        y=landmark_groundtruth[:, 2],
        marker=dict(
            color='LightSkyBlue',
            size=8,
            line=dict(
                color='MediumPurple',
                width=2
            )
        ),
        name='Landmarks'
    )
)
fig.show()

In [32]:
# make an empty figure
fig_dict = {
    "data": [],
    "layout": {},
    "frames": []
}

# fill in most of layout
fig_dict["layout"]["xaxis"] = {"range": [-2, 6], "title": "x [m]"}
fig_dict["layout"]["yaxis"] = {"range": [-6, 7], "title": "y [m]"}
fig_dict["layout"]["hovermode"] = "closest"
fig_dict["layout"]["updatemenus"] = [
    {
        "buttons": [
            {
                "args": [
                         None,
                         {
                             "frame": {"duration": 10, "redraw": False},
                             "fromcurrent": True,
                             "transition": {"duration": 0, "easing": "quadratic-in-out"}
                         }
                        ],
                "label": "Play",
                "method": "animate"
            },
            {
                "args": [
                         [None],
                         {
                             "frame": {"duration": 0, "redraw": False},
                             "mode": "immediate",
                             "transition": {"duration": 0}
                         }
                        ],
                "label": "Pause",
                "method": "animate"
            }
        ],
        "direction": "left",
        "pad": {"r": 10, "t": 87},
        "showactive": False,
        "type": "buttons",
        "x": 0.1,
        "xanchor": "right",
        "y": 0,
        "yanchor": "top"
    }
]

sliders_dict = {
    "active": 0,
    "yanchor": "top",
    "xanchor": "left",
    "currentvalue": {
        "font": {"size": 20},
        "prefix": F"Time(1 unit for {timesteps_per_frame * sample_time} second):",
        "visible": True,
        "xanchor": "right"
    },
    "transition": {"duration": 300, "easing": "cubic-in-out"},
    "pad": {"b": 10, "t": 50},
    "len": 0.9,
    "x": 0.1,
    "y": 0,
    "steps": []
}

def robot_data(i, k):
    data = robots_data[F'robot{i}_groundtruth']
    info = []
    location = {
        "x": [data[k, 1]],
        "y": [data[k, 2]],
        "mode": "markers",
        "marker": {"size": 13, "line": {"color": "black", "width": 2}},
        "name": F"robot{i}"
    }
    info.append(location)
    return info

# robots initial location
for i in range(1, n_robots + 1):
    fig_dict["data"].extend(robot_data(i, 0))
    
num_frames = timesteps // timesteps_per_frame
for k in range(num_frames):
    time = k * timesteps_per_frame * sample_time
    frame = {"data": [], "name": str(k)}
    for i in range(1, n_robots + 1):
        frame["data"].extend(robot_data(i, k * timesteps_per_frame))
    fig_dict["frames"].append(frame)
    slider_step = {
        "args": [
            [k],
            {
                "frame": {"duration": 20, "redraw": False},
                "mode": "immediate",
                "transition": {"duration": 0}
            }
        ],
        "label": k,
        "method": "animate"
    }
    sliders_dict["steps"].append(slider_step)
fig_dict["layout"]["sliders"] = [sliders_dict]

fig = go.Figure(fig_dict)
fig.add_trace(
    go.Scatter(
        mode='markers',
        x=landmark_groundtruth[:, 1],
        y=landmark_groundtruth[:, 2],
        marker=dict(
            color='LightSkyBlue',
            size=8,
            line=dict(
                color='MediumPurple',
                width=2
            )
        ),
        name='Landmarks'
    )
)
fig.show()